### Final Project - Simulating Fluid Vortices using Latice Boltzmann Method (LBM)
Author: Richard Saeed 

Due: The week of 11.28.23 

Group: A (Lab section Tuesday 12-2:00 pm) 


#### ---------- Source Material --------------
General methodology for LBM: https://en.wikipedia.org/wiki/Lattice_Boltzmann_methods 

Applied concent: https://ncbi.nlm.nih.gov/pmc/articles/PMC7605305/     

#### Main Source
2D LBM Methodology + in depth information: https://link.springer.com/chapter/10.1007/978-3-319-44649-3_3


#### ----------- Goals ------------
1. Code constants + boundary conditions + inflow + outflow(?)                     
   Note: May create inflows for both sides of the mesh grid, goal to simulate fluid mixing.
   
2. Determine density and velocities of particles (macroscopic scale)
3. Expand on step (1) to apply the boundaries via Zou-He method (see main source above)
4. Determine the discrete velocities   Note: See main source section 2.2 (revisit)
5. Determine collision parameters and deflection 
   (deflection pertains to any obstacle-- if no obstacle, ignore this step).
6. Iterate through N times (adjust N as needed)
{Add additional goals}






In [1]:
import matplotlib.pyplot as plt
import numpy as np 
import cmasher as cmr
from matplotlib.animation import FFMpegWriter
%matplotlib qt

### Initial Conditions

In [2]:
Nx = 450
Ny = 100
tau = 0.53                                                     # kinematic viscosity / timescale (τ aka relaxation time)
Nt = 5000                                                      # number of iterations
skip_N = 25

# -------- lattice velocities & weights ----------------
NL = 9                                                         # Nine discrete lattice velocities
cxs = np.array([0, 0, 1, 1, 1, 0, -1, -1, -1])
cys = np.array([0, 1, 1, 0,-1,-1, -1,  0,  1])
weights = np.array([4/9,                                       
                    1/9, 1/36, 1/9, 1/36, 
                    1/9, 1/36, 1/9, 1/36])                     # Weights are essentially the probability of a particle moving to a certain node   


# --------- defining initial conditions -------- 
'''mesoscopic velocities, velocity of every lattice in each of the
   lattice's nodes. See Spinger section 3.3.3 for np.ones over np.zeros.
   fi is a 3D array, 2D for each lattice (i,j), then an additional dimension for
   each one of the lattice's velocities'''
fi = np.ones((Ny, Nx, NL)) + 0.01 * np.random.rand(Ny, Nx, NL)

'''fi[...,3] initial vel to the right, iterates through every lattice
   and assigns a velocity to the 3rd node, i.e. (1, 0) = velocity'''
fi[:, :, 3] = 1.8                                              # initially set to 2.3, this resulted in a runtime error (crashed simulation, see animation3.mp4)          

# --------- define obstacle(s) ---------------
'''Created an array that maps to every lattice in the domain and assigns it
   True/False. If False, the point is empty space, True then the value is an obstacle.'''

square = np.full((Ny, Nx), False)
square_size = 30
for j in range(0, Ny):
    for i in range(0, Nx):
        if (Nx//9 < i < Nx//9 + square_size) and (Ny//3 < j < Ny//3 + square_size):
            square[j][i] = True
            
square_size2 = 15
for j in range(0, Ny):
    for i in range(0, Nx):
        if (Nx//2.5 < i < Nx//2.5 + square_size2) and (Ny//2 < j < Ny//2 + square_size2):
            square[j][i] = True
            
square_size3 = 22
for j in range(0, Ny):
    for i in range(0, Nx):
        if (Nx//1.5 < i < Nx//1.5 + square_size3) and (Ny//4 < j < Ny//4 + square_size3):
            square[j][i] = True


### Main Loop

#### Change the number of iterations in the above cell, Nt in line 4
#### Can change inflow velocity in line 25 above, when fi[...,3] > 2.3, the simulation may result in runtime error (see animation3.mp4)
#### Can change bitrate and codec as needed in line 4 of the cell below.
####

In [3]:
# --------- .mp4 configurations -------
fig = plt.figure(figsize = (15, 8), dpi = 60)
metadata = dict(title='vortices via LBM', artist='Matplotlob',comment='None')
writer = FFMpegWriter(fps=20, metadata=metadata, bitrate=2_000_000, codec='h264')
with writer.saving(fig,'test1.mp4', dpi=60):
    
#     --------- main loop -----------------
    # plt.style.use('dark_background')
    for iterate in range(Nt):

        if iterate%500 == 0:
            print(iterate)
        if (iterate + 1) == Nt:
            print('Finished Iterating')

        # ----- Zou & He boundary conditions ---------
        '''Sets the values at the very end of the outflow to the value
           right before it, effectively canceling out. Functionally, this
           method prevents reflections from the inflow/outflow. The only
           remaining waves should be those reflecting off the upper/lower
           boundaries. Comment out lines 23, 24 to see how the simulation 
           is effected.'''
        fi[:, -1, 6:9] = fi[:, -2, 6:9]
        fi[:,  0, 2:5] = fi[:,  1, 2:5]

        for i in range(NL):
            '''Streaming, moves every node velocity in the direction of its
               neighbor. Rather, streaming the velocities to sister-nodes
               and lattices. Iterates through every node (x,y) and rolls in
               the direction of its corresponding discrete velocity. 
               Springer ch. 13, regarding np.roll()'''
            cx, cy = cxs[i], cys[i]
            fi[:, :, i] = np.roll(fi[:, :, i], (cy, cx), axis=(0,1))

        '''Setting all velocities within/touching a boundary to
           its opposite velocity, thereby reflecting off said boundary.'''
        boundaryF = fi[square, :]
        boundaryF = boundaryF[:, [0, 5, 6, 7, 8,   
                                     1, 2, 3, 4]] 

        # -------- fluid ----------
        '''Density (ρ) sums over the last axis (contains velocities),
           where ux, uy are the momenta, rather, the macroscopic velocities.'''
        rho = np.sum(fi, 2)                   # NOTE: Changed variable ρ to "rho" --- ρ was giving runtime errors??          
        ux = np.sum(fi * cxs, 2) / rho        
        uy = np.sum(fi * cys, 2) / rho

        # -------- boundary --------
        '''Setting all velocities inside the boundary to zero
           so there is no movement within the solid object(s).'''
        fi[square, :] = boundaryF
        ux[square], uy[square] = 0, 0         # macroscopic velocities within a boundary = 0 (no movement)

        # ------- collision, BGK method ------
        '''define f_equilibrium then omega (Ω BGK collision opperator)
          •let (c_s)^2 = 1/3 - refer to Springer pg. 416. for 
           f_eq, refer to pg. 64 equation 3.4'''
        f_eq = np.zeros(fi.shape)
        for i in range(NL):
            cx, cy, w = cxs[i], cys[i], weights[i]
            f_eq[:, :, i] = w * rho * (1 + 3 * (ux * cx + uy * cy) +
                                     9 * (ux * cx + uy * cy)**2 / 2 -
                                     3 * (ux**2 + uy**2) / 2)

        '''solve the discretized Boltzmann Eq. to determine next timestep ∆t, 
           pg. 64, equations 3.2 & 3.3'''
        omega = (-1) * (fi - f_eq) / tau
        fi = fi + omega
        magnitude_u = np.sqrt(ux**2 + uy**2)  # recall u = macroscopic velocities

        #------- calculating curl --------
        dudx, dudy = np.gradient(ux)
        dvdx, dvdy = np.gradient(uy)
        # curl = (dvdy- dudx)
        curl = dudx - dvdy

        # ------ plotting -------
        if(iterate%skip_N == 0):
            plt.clf() # comment when testing

            # plotting magnitude of macroscopic velocities ||u||
            plt.subplot(211)
            plt.imshow(magnitude_u,
                       cmap = cmr.sapphire
                      )
            plt.colorbar(orientation='horizontal').set_label('Velocity Magnitude')

            # plotting Vorticity Magnitude
            plt.subplot(212)
            plt.imshow(curl,
                       cmap='bwr',
                       vmin=-0.035,
                       vmax=0.035
                      )
            plt.colorbar(orientation = 'horizontal').set_label('Vorticity Magnitude')

            plt.show()
            plt.draw()               # comment for testing
            plt.pause(0.0001)
            writer.grab_frame()      # comment for testing
            # plt.clf()              # comment when ready to create .mp4, uncomment for testing

0
500
1000
1500
2000
2500
3000
3500
4000
4500
Finished Iterating
